# Simple Pay-As-You-Go Accounting for SaaS


While building saas products, especially one like [AllBox](https://allbox.in), people pay to use your software. A lot of our software is billed pay-as-you-go where people only pay for what they have used, not a blanket cover-all cost. This post is about how one would model such a system in a very minimal / simple way and it invites discussion about how to best handle this situation.

If you're not familiar with the basics of accounting [Beancount](https://beancount.github.io/docs/index.html) and [Plain text accounting](https://plaintextaccounting.org/) are good places to start

First let's describe the problem we are out to solve.

## Parts

- Our `application` is what we are building. It could be anything at all and for the purposes of this post we assume a simple web application.
- A `gateway` is something that accepts payments on your behalf from customers via multiple methods of payment and then finally send the money to you. For this post we assume [Razoypay](https://razorpay.com).
- A `customer` is someone who pays you money in order to use your `application`.

## Goals

1. We cannot **LOSE** or **CREATE** money.
    - See [the British Post Office Scandal](https://en.wikipedia.org/wiki/British_Post_Office_scandal) or [the Synapse fiasco](https://www.bloomberg.com/opinion/articles/2024-11-25/synapse-still-can-t-find-its-money) to see how real lives get impacted due to faults in accounting systems.
2. We cannot hold invalid amounts of money. For example 0.5 (cents or paise) do not exist so we cannot operate on them.
3. If we every want to, we should be able to trace every single amount and figure out where it went.

## Why not Tally / Quickbooks etc ?

There are a few lines of thought we went through:

1. This will introduce a new services into our tech stack. We don't want that since **Goal 3** will be dependent on how well supported debugging is in those tools. We absolutely do not want to go debugging using account statement sheets as our ONLY tool. We also want to keep our stack simple:
    - https://thmsmlr.com/cheap-infra
    - https://www.amazingcto.com/postgres-for-everything/
    - https://boringtechnology.club/
2. Interacting with any 3rd party system will involve some sort of communication. APIs / SDKs etc.
    - Communnication failure means that we will have more moving parts, making debugging hard.
    - Failures can also happen on the 3rd party side due to no fault of our own and we're left wondering if we'll ever get any customer support.
    - If we get caught in an inconsistent communication state, it can conflict with **Goal 1** and we might create/destroy money.
3. We don't want to mix our company accounting with SaaS accounting. For example HR / Payroll has nothing to do with the product `customer` accounting and so should remain separate. Our goal is to make sure that customers should only pay for what they consume and vice versa. Nothing more.


## What should we definitely do?

1. Everything should be immutable. We don't want to lose information EVER when it comes to money.
2. Use normal accounting terminology so that when needed company accountants can review and help us debug.
3. Make sure we can show balances / statements / breakdowns of expenses for each client whenever required.
4. Automate the entire process so that we don't need manual intervention at any point.

## The solution

We create 3 tables in our database.

```
Account {
  id        integer [primary key]
  name      string
  user_id   integer
}

Transaction {
  id        integer [primary key]
  refno     varchar
  metadata  JSON
}

Posting {
  id        integer [primary key]
  refno     varchar
  amount    integer
  metadata  JSON
  // -------FOREIGN KEYS
  txid      Transaction(id)
  accid     Account(id)
}

```

Note that the `Account` table is not your SAAS account. It represents "accounting" accounts.
With this we create a few entries in the `Account` table to represent "accounting" accounts. Each account has a name and is potentially linked to a user_id indicating that it belongs to that user. Accounts that don't belong to any particluar user don't have user_id associated with them. Accounts with `<user_id>` in each of them are created with a foreign key to the given user. Remaining accounts are having user_id = null.

- `Income/Customer/<user_id>` : Used to represent the customer's money. This account will almost always have a negative balance
- `Income/Razorpay` : Used to represent our payment processor.
- `Assets/Customer/<user_id>` : Used to represent an individual customer's wallet on our application.
- `Expense/Razorpay` : Used to represent the fees we pay to razorpay. It's usually some % of the transaction amount. This account will almost always have a positive balance.
- `Expense/<service>/<user_id>` : This is used to repsent services inside our system that the customer is using. For example, storage , network etc. These accounts will tend to be positive balance.




## Workflows



## Customers pays Razorpay

- Let's say a customer (with id=1000) wants to give us INR 100 to use our product. They will transfer this amount to Razorpay via their debit card / internet banking / UPI etc.
- We note this down in our accounts by creating a single `Transaction` row.
- For this `Transaction` we create two `Posting` rows.
    - `Income/Customer/1000      INR -100` representing the money leaving customer's bank account.
    - `Income/Razorpay           INR +100` representing the money being received by Razorpay.

## Razorpay pays Us

- Razorpay usually takes a few days to transfer the money to us and they make a single transfer per-day. For example let's assume that two customers have paid INR 100, and INR 150 to Razorpay.
- After 3 days Razorpay transfers this to our bank accounts, after it deducts it's own fees . So in total only INR 245 actually reaches our bank accounts.
- We again create a single `Transaction` entry to represent this process.
- For this `Transaction` we create the following `Posting` entries.
    - `Income/Razorpay           INR -250` showing the money leaving razorpay's accounts.
    - `Expense/Razorpay          INR +  5` showing the fees we have paid to razorpay.
    - `Assets/Customer/1000      INR + 98` showing how much money has to be added to customer wallet.
    - `Assets/Customer/1001      INR +147` showing how much money went into the second customer's wallet. 

## Customer consumes Services

- Now that the money has reached the customer's wallet, they can begin using our services.
- In our products we don't actually wait for the customer's money to reach us. Each customer has a bit of "goodwill" and so they can over-consume services. You might/might not want to implement this in your application.

Now, how to actually "consume" services.

- Every time we provide a service to the customer we can then deduct money from their wallet.
- For example a customer stores some files with us. We can call this service 'storage' and we want to charge them per-GB of data stored with us. Let us say they have stored 3 GB of data with us and we want to charge them INR 3 for this.
- To represent this we first create a `Transaction` record.
- Then we create postings to record the service usage:
    - `Assets/Customer/1000      INR -3` representing the money leaving the customer wallet.
    - `Expense/Storage/1000      INT +3` representing the service account receiving money in exchange for supplying the service.
    
    
By creating this per-service-per-customer account we also retain information about which of our services are being used to what extent by our customers.


# Operations

## Wallet balance

- At any given point in time you can simply sum the postings related to a given `Account` to get it's balance.
- Since running `sum` can get expensive if this is a frequent operation in your `application`, you can introduce [Clearing Wallets](https://beancount.github.io/docs/sharing_expenses_with_beancount.html#clearing-asset-accounts) into the workflows and that should make calculations faster.

## Statements

- You can simply select `transaction` entries between certain dates and filter to certain `Account` entries that you are interested in and you can get statements for any account.

## Tracking where the money went

- Since we store `meta` in both `posting` and `transaction` tables, you can use this info to track where certain money went.
- For example a razorpay transaction ID can be tracked from `Income/Customer/1000 -> Income/Razorpay -> Assets/Customer/1000` easily by filtering on `meta` fields using [JSON filtering](https://www.postgresql.org/docs/current/functions-json.html)

## How much have we earned?

- We can sum all balances for `Income/Customer/*` accounts and know the total money that customers have paid us.
- Similarly we can sum all balances for `Expenses/*/*` to know how much customers have 'consumed'. If this is proportional to what our actual expenses are to run the platform we can estimate our actual 'expenses'.
- Summing the balances of `Assets/Customer/*` will tell us how much money is in our bank that is not yet 'consumed' by customers.


# Conclusion

This kind of setup is very easy to create in hindsight and works very well for a lot of simple operations. Perhaps you would like to add something? Do email in your comments :D